In [45]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns
from scipy import stats
from datetime import timedelta, datetime
import psycopg2 as psy
import math
import itertools
from queue import LifoQueue, Queue, PriorityQueue
import collections
from  sklearn.utils import shuffle
from plotnine import * 
from random import uniform

In [7]:
conn = psy.connect("host=134.122.24.175" + " dbname=sec_edgar" + " user=chubak" +
                         " password=R3n0_Nevada")

cur = conn.cursor()

In [8]:
cur.execute("SELECT * FROM holdings_xml")

all_rec = cur.fetchall()

df_all = pd.DataFrame.from_records(all_rec, columns=[x[0] for x in cur.description])



In [9]:
def previous_quarter(ref):
  if ref.month < 4:
      return datetime(ref.year - 1, 12, 31).date()
  elif ref.month < 7:
      return datetime(ref.year, 3, 31).date()
  elif ref.month < 10:
      return datetime(ref.year, 6, 30).date()
  return datetime(ref.year, 9, 30).date()

df_all["date_trunc"] = pd.to_datetime(df_all["date"]).map(previous_quarter)

df_all

code                    nameofissuer  ...         cik  date_trunc
0          123                    ALPHABET INC  ...  0001647251  2018-06-30
1          124                    ALPHABET INC  ...  0001647251  2018-06-30
2          125             CANADIAN PAC RY LTD  ...  0001647251  2018-06-30
3          126    CHARTER COMMUNICATIONS INC N  ...  0001647251  2018-06-30
4          127                      ALTABA INC  ...  0001647251  2018-06-30
...        ...                             ...  ...         ...         ...
139130  139253                Altria Group Inc  ...  0001360079  2018-12-31
139131  139254     Consolidated Tomoka Land Co  ...  0001360079  2018-12-31
139132  139255  Liberty Media Corp-Liberty For  ...  0001360079  2018-12-31
139133  139256       Union Pacific Corporation  ...  0001360079  2018-12-31
139134  139257       Liberty Latin America Ltd  ...  0001360079  2018-12-31

[139135 rows x 15 columns]

In [ ]:
frequency_ls = []

for name, group in df_all.groupby("date_trunc"):
  tups = []
  for cik1 in group["cik"].unique():
    for cik2 in group["cik"].sort_index(ascending=False).unique():
      print(f"Doing {cik1}-{cik2}")

      cusips_1 = group[group["cik"] == cik1].loc[:, "cusip"]
      cusips_2 = group[group["cik"] == cik2].loc[:, "cusip"]
      concat = pd.concat([cusips_1, cusips_2])
      unique = np.unique(concat, return_counts=True)
      max = len([u for u in unique[1] if u >= 2])
      tups.append((cik1, cik2, max))



  
  df_tup = pd.DataFrame.from_records(tups, columns=["cik_x", "cik_y", "freq"])
  df_tup["freq"] = pd.to_numeric(df_tup["freq"])
  df_tup = df_tup.sort_values(by=["freq"])

  fig = plt.figure()


  p = ggplot(df_tup, aes('cik_x', 'cik_y')) + geom_tile(aes(fill='freq'))\
    + scale_fill_gradientn(colors=['#9ebcda','#8c6bb1','#88419d','#6e016b', "#8c139d", "#2f132d", "#1a232c"]) \
    + ggtitle(f"Heatmap of {name}") + geom_text(aes(label='freq'), size=0.4) \
    + theme(axis_text_x = element_text(face="bold", color="#993333", 
                           size=0.8, angle=45),
          axis_text_y = element_text(face="bold", color="#993333", 
                           size=0.8, angle=45))

  ggsave(plot=p, filename=f"{name}.png", dpi=1200)

  del tups
  del df_tup

  





Doing 0001569205-0001340807
Doing 0001569205-0001061186
Doing 0001569205-0001569205
Doing 0001061186-0001340807
Doing 0001061186-0001061186
Doing 0001061186-0001569205
Doing 0001340807-0001340807
Doing 0001340807-0001061186
Doing 0001340807-0001569205


/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:729: PlotnineWarning:

Saving 6.4 x 4.8 in image.

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:730: PlotnineWarning:

Filename: 2013-03-31.png

/usr/local/lib/python3.6/dist-packages/plotnine/utils.py:1246: FutureWarning:

is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead



Streaming output truncated to the last 5000 lines.
Doing 0001358706-0001568820
Doing 0001358706-0001325256
Doing 0001358706-0001276537
Doing 0001358706-0000905567
Doing 0001358706-0001166559
Doing 0001358706-0001133219
Doing 0001358706-0001456417
Doing 0001358706-0001106500
Doing 0001358706-0000807985
Doing 0001358706-0001115373
Doing 0001358706-0001562810
Doing 0001358706-0001360079
Doing 0001358706-0000883965
Doing 0001358706-0001112520
Doing 0001358706-0001128239
Doing 0001358706-0000947996
Doing 0001358706-0001136704
Doing 0001358706-0001569205
Doing 0001358706-0001325447
Doing 0001358706-0001058854
Doing 0001358706-0000943518
Doing 0001358706-0001314620
Doing 0001358706-0001353312
Doing 0001358706-0001483866
Doing 0001358706-0001389403
Doing 0001358706-0001106129
Doing 0001358706-0001167483
Doing 0001358706-0001542300
Doing 0001358706-0001142062
Doing 0001358706-0001145020
Doing 0001358706-0001410352
Doing 0001358706-0001061165
Doing 0001358706-0001027796
Doing 0001358706-00009456

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:729: PlotnineWarning:

Saving 6.4 x 4.8 in image.

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:730: PlotnineWarning:

Filename: 2013-06-30.png

/usr/local/lib/python3.6/dist-packages/plotnine/utils.py:1246: FutureWarning:

is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead



Streaming output truncated to the last 5000 lines.
Doing 0001313926-0001339161
Doing 0001313926-0001353312
Doing 0001313926-0001336800
Doing 0001313926-0001115373
Doing 0001313926-0001106500
Doing 0001313926-0001421669
Doing 0001313926-0001061165
Doing 0001313926-0000732905
Doing 0001313926-0000943518
Doing 0001313926-0001106129
Doing 0001313926-0000905567
Doing 0001313926-0000846222
Doing 0001313926-0001340807
Doing 0001313926-0001027796
Doing 0001313926-0001103804
Doing 0001313926-0001136704
Doing 0001313926-0001314620
Doing 0001313926-0001263508
Doing 0001313926-0001472322
Doing 0001313926-0000820124
Doing 0001313926-0001145020
Doing 0001313926-0001456417
Doing 0001313926-0001166559
Doing 0001313926-0001313926
Doing 0001313926-0001568820
Doing 0001313926-0000860643
Doing 0001313926-0001562810
Doing 0001313926-0001542300
Doing 0001313926-0001410352
Doing 0001313926-0000883965
Doing 0001313926-0000934639
Doing 0001313926-0001112520
Doing 0001313926-0001541996
Doing 0001313926-00013895

...

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:23: RuntimeWarning:

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:729: PlotnineWarning:

Saving 6.4 x 4.8 in image.

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:730: PlotnineWarning:

Filename: 2019-12-31.png

/usr/local/lib/python3.6/dist-packages/plotnine/utils.py:1246: FutureWarning:

is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:363: RuntimeWarning:

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (

Streaming output truncated to the last 5000 lines.
Doing 0001336528-0000732905
Doing 0001336528-0001336800
Doing 0001336528-0001115373
Doing 0001336528-0001404574
Doing 0001336528-0001535264
Doing 0001336528-0001389403
Doing 0001336528-0001542302
Doing 0001336528-0000351262
Doing 0001336528-0001471085
Doing 0001336528-0000200217
Doing 0001336528-0000098758
Doing 0001336528-0001106500
Doing 0001336528-0001040273
Doing 0001336528-0001597864
Doing 0001336528-0001061186
Doing 0001336528-0001377817
Doing 0001336528-0000945631
Doing 0001336528-0000846222
Doing 0001336528-0001747057
Doing 0001336528-0001608485
Doing 0001336528-0001524362
Doing 0001336528-0001745214
Doing 0001336528-0001542300
Doing 0001336528-0001671657
Doing 0001336528-0001138995
Doing 0001336528-0001103804
Doing 0001336528-0001752148
Doing 0001336528-0001325256
Doing 0001336528-0001569205
Doing 0001336528-0001697591
Doing 0001336528-0001353312
Doing 0001336528-0001599383
Doing 0001336528-0001145020
Doing 0001336528-00018002

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:23: RuntimeWarning:

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:729: PlotnineWarning:

Saving 6.4 x 4.8 in image.

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:730: PlotnineWarning:

Filename: 2020-03-31.png

/usr/local/lib/python3.6/dist-packages/plotnine/utils.py:1246: FutureWarning:

is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:363: RuntimeWarning:

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (

Streaming output truncated to the last 5000 lines.
Doing 0001389403-0001704404
Doing 0001389403-0001325256
Doing 0001389403-0001145020
Doing 0001389403-0000096223
Doing 0001389403-0001166559
Doing 0001389403-0001549575
Doing 0001389403-0001641864
Doing 0001389403-0001389403
Doing 0001389403-0001635663
Doing 0001389403-0001027796
Doing 0001389403-0001058854
Doing 0001389403-0001040273
Doing 0001389403-0000846222
Doing 0001389403-0000098758
Doing 0001389403-0001697591
Doing 0001389403-0001771122
Doing 0001389403-0001389563
Doing 0001389403-0001671657
Doing 0001389403-0001601160
Doing 0001389403-0001167483
Doing 0001389403-0001629996
Doing 0001389403-0000883965
Doing 0001389403-0001539436
Doing 0001389403-0001631664
Doing 0001389403-0001358706
Doing 0001389403-0001070134
Doing 0001389403-0001752148
Doing 0001389403-0001591986
Doing 0001389403-0001105497
Doing 0001389403-0001103804
Doing 0001389403-0001471085
Doing 0001389403-0001404599
Doing 0001389403-0000813917
Doing 0001389403-00016978

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:23: RuntimeWarning:

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:729: PlotnineWarning:

Saving 6.4 x 4.8 in image.

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:730: PlotnineWarning:

Filename: 2020-06-30.png

/usr/local/lib/python3.6/dist-packages/plotnine/utils.py:1246: FutureWarning:

is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead

/usr/local/lib/python3.6/dist-packages/plotnine/ggplot.py:363: RuntimeWarning:

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (